In [2]:
import tensorflow as tf
import tensorflow_ranking as tfr
import collections
import numpy as np
from typing import Dict, List, Optional, Text, Tuple
import tensorflow_datasets as tfds
import pprint

In [3]:
import pandas as pd

In [4]:
import tensorflow_ranking as tfr
import tensorflow_recommenders as tfrs

In [5]:
doc = pd.read_csv('doc.csv')

In [6]:
doc.head()

doc_id                                               body
0  MED-1  birth weight , head circumference , prenatal e...
1  MED-2  a statistical regression model estimation acry...
2  MED-3  chronic intake potato chips humans increases p...
3  MED-4  dietary patterns breast cancer risk women . - ...
4  MED-5  empirically derived dietary patterns risk post...

In [7]:
train_relevance_file = 'train.qrel'
test_relevance_file = 'test.qrel'
dev_relevance_file = 'dev.qrel'

In [8]:
relevance_columns = ['query_id', 'doc_id', 'relevance']
relevance_data_train = pd.read_csv(train_relevance_file, sep=' ',  header=None, names=relevance_columns)
relevance_data_test = pd.read_csv(test_relevance_file, sep=' ',  header=None, names=relevance_columns)
relevance_data_dev = pd.read_csv(dev_relevance_file, sep=' ',  header=None, names=relevance_columns)

In [9]:
queries = pd.read_csv('query.csv')

In [10]:
queries

query_id                                              query
0     PLAIN-2429  diverticulosis : when our most common gut diso...
1     PLAIN-2439  from table to able : combating disabling disea...
2     PLAIN-2449    how to make your own fruit and vegetable wash\n
3     PLAIN-2459                          how to prevent a stroke\n
4     PLAIN-2469  if white rice is linked to diabetes , what abo...
...          ...                                                ...
3239   PLAIN-956                                  cooking methods\n
3240   PLAIN-966                                         cortisol\n
3241   PLAIN-977                                       crib death\n
3242   PLAIN-987                                            cumin\n
3243   PLAIN-997                                   czechoslovakia\n

[3244 rows x 2 columns]

In [11]:
doc

doc_id                                               body
0        MED-1  birth weight , head circumference , prenatal e...
1        MED-2  a statistical regression model estimation acry...
2        MED-3  chronic intake potato chips humans increases p...
3        MED-4  dietary patterns breast cancer risk women . - ...
4        MED-5  empirically derived dietary patterns risk post...
...        ...                                                ...
5366  MED-5367  the relationship plasma carotenoids depressive...
5367  MED-5368  suicide mortality relation dietary intake n-3 ...
5368  MED-5369  suicide mortality european union . - pubmed - ...
5369  MED-5370  long chain omega-3 fatty acids intake , fish c...
5370  MED-5371  omega-3 fatty acids treatment depression : sys...

[5371 rows x 2 columns]

In [12]:
relevance_data_train

query_id    doc_id  relevance
0          PLAIN-3  MED-2436          3
1          PLAIN-3  MED-2437          3
2          PLAIN-3  MED-2438          3
3          PLAIN-3  MED-2439          3
4          PLAIN-3  MED-2440          3
...            ...       ...        ...
139345  PLAIN-3474  MED-3546          2
139346  PLAIN-3474  MED-3547          2
139347  PLAIN-3474  MED-4632          2
139348  PLAIN-3474  MED-4633          2
139349  PLAIN-3474  MED-4634          2

[139350 rows x 3 columns]

In [13]:
def add_q_and_d(relevance_data, queries, doc):
    merged_df = pd.merge(relevance_data, doc, on='doc_id', how='left')
    merged_df = pd.merge(merged_df, queries, on='query_id', how='left')
    merged_df['query'] = merged_df['query'].astype(str)
    merged_df['relevance'] = merged_df['relevance'].astype(str)
    return merged_df


In [14]:
train_df = add_q_and_d(relevance_data_train, queries, doc)
test_df = add_q_and_d(relevance_data_test, queries, doc)
dev_df = add_q_and_d(relevance_data_dev, queries, doc)

In [15]:
data = train_df[['query', 'body', 'relevance']]

In [16]:
data_test = test_df[['query', 'body', 'relevance']]

In [17]:
data_dev = dev_df[['query', 'body', 'relevance']]

In [18]:
dataset = tf.data.Dataset.from_tensor_slices((data))

In [19]:
dataset_test = tf.data.Dataset.from_tensor_slices((data_test))

In [20]:
dataset_dev = tf.data.Dataset.from_tensor_slices((data_dev))

In [21]:
dataset

<_TensorSliceDataset element_spec=TensorSpec(shape=(3,), dtype=tf.string, name=None)>

In [22]:
train_df

query_id    doc_id relevance  \
0          PLAIN-3  MED-2436         3   
1          PLAIN-3  MED-2437         3   
2          PLAIN-3  MED-2438         3   
3          PLAIN-3  MED-2439         3   
4          PLAIN-3  MED-2440         3   
...            ...       ...       ...   
139345  PLAIN-3474  MED-3546         2   
139346  PLAIN-3474  MED-3547         2   
139347  PLAIN-3474  MED-4632         2   
139348  PLAIN-3474  MED-4633         2   
139349  PLAIN-3474  MED-4634         2   

                                                     body  \
0       content low density lipoprotein receptors brea...   
1       diet breast cancer : understanding risks benef...   
2       the association dietary lignans , phytoestroge...   
3       plant sterols anticancer nutrients : evidence ...   
4       total cholesterol cancer risk large prospectiv...   
...                                                   ...   
139345  elevated monoamine oxidase levels brain : expl...   
139346  monoamine theories depression : historical imp...   
139347  the effect vegetarian diets plasma lipid plate...   
139348  vegetarian diets healthy mood states : cross-s...   
139349  fatty acid profile human saliva : indicator di...   

                                            query  
0       breast cancer cells feed on cholesterol\n  
1       breast cancer cells feed on cholesterol\n  
2       breast cancer cells feed on cholesterol\n  
3       breast cancer cells feed on cholesterol\n  
4       breast cancer cells feed on cholesterol\n  
...                                           ...  
139345             fish consumption and suicide\n  
139346             fish consumption and suicide\n  
139347             fish consumption and suicide\n  
139348             fish consumption and suicide\n  
139349             fish consumption and suicide\n  

[139350 rows x 5 columns]

In [23]:
def cttf(df):
    df['relevance'] = df['relevance'].astype(str)
    tf_obj = tf.convert_to_tensor(df)
    return tf_obj

In [24]:
tf_train = cttf(train_df)

In [25]:
tf_train

<tf.Tensor: shape=(139350, 5), dtype=string, numpy=
array([[b'PLAIN-3', b'MED-2436', b'3',
        b'content low density lipoprotein receptors breast cancer tissue related survival patients . abstract the content low density lipoprotein ( ldl ) receptors tissue primary breast cancers determined prognostic information compared variables established prognostic importance . frozen tumour specimens selected , tissue 72 patients ( 32 died ) studied . the ldl receptor content showed inverse correlation survival time . analysis multivariate statistical method showed presence axillary metastasis , content receptors oestrogen ldl , diameter tumour , dna pattern prognostic regard patient survival . improved methods predicting survival time patients breast cancer choice treatment individual patients .',
        b'breast cancer cells feed on cholesterol\n'],
       [b'PLAIN-3', b'MED-2437', b'3',
        b'diet breast cancer : understanding risks benefits . - pubmed - ncbi abstract background : br

In [26]:
tf_test = cttf(test_df)

In [27]:
tf_dec = cttf(dev_df)

In [28]:
unique_queries = list(set(queries['query']))

In [29]:
unique_docs =list(set(doc['body']))

In [30]:
type(tf_dec)

tensorflow.python.framework.ops.EagerTensor

In [31]:
dataset = dataset.map(lambda x: {
    "body": x[1],
    "query": x[0],
    "relevance": x[2],
})

In [32]:
dataset_test = dataset_test.map(lambda x: {
    "body": x[1],
    "query": x[0],
    "relevance": x[2],
})

In [33]:
dataset_dev = dataset_dev.map(lambda x: {
    "body": x[1],
    "query": x[0],
    "relevance": x[2],
})

In [34]:
for x in dataset:
    print(x["relevance"])

tf.Tensor(b'3', shape=(), dtype=string)
tf.Tensor(b'3', shape=(), dtype=string)
tf.Tensor(b'3', shape=(), dtype=string)
tf.Tensor(b'3', shape=(), dtype=string)
tf.Tensor(b'3', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)
tf.Tensor(b'2', shape=(), dtype=string)


In [35]:
def _create_feature_dict() -> Dict[Text, List[tf.Tensor]]:
  """Helper function for creating an empty feature dict for defaultdict."""
  return {"query": [], "body": [], "relevance": []}

In [36]:
def _sample_list(
    feature_lists: Dict[Text, List[tf.Tensor]],
    num_examples_per_list: int,
    random_state: Optional[np.random.RandomState] = None,
) -> Tuple[tf.Tensor, tf.Tensor]:
  """Function for sampling a list example from given feature lists."""
  if random_state is None:
    random_state = np.random.RandomState()

  sampled_indices = random_state.choice(
      range(len(feature_lists["body"])),
      size=num_examples_per_list,
      replace=True,
  )
#   print(len(feature_lists["relevance"]), sampled_indices)
  sampled_movie_titles = [
      feature_lists["body"][idx] for idx in sampled_indices
  ]
  sampled_ratings = [
      feature_lists["relevance"][idx]
      for idx in sampled_indices
  ]

  return (
      tf.stack(sampled_movie_titles, 0),
      tf.stack(sampled_ratings, 0),
  )

In [37]:
def sample_listwise(
    rating_dataset: tf.data.Dataset,
    num_list_per_user: int = 10,
    num_examples_per_list: int = 10,
    seed: Optional[int] = None,
) -> tf.data.Dataset:
  """Function for converting the MovieLens 100K dataset to a listwise dataset.

  Args:
      rating_dataset:
        The MovieLens ratings dataset loaded from TFDS with features
        "movie_title", "user_id", and "user_rating".
      num_list_per_user:
        An integer representing the number of lists that should be sampled for
        each user in the training dataset.
      num_examples_per_list:
        An integer representing the number of movies to be sampled for each list
        from the list of movies rated by the user.
      seed:
        An integer for creating `np.random.RandomState`.

  Returns:
      A tf.data.Dataset containing list examples.

      Each example contains three keys: "user_id", "movie_title", and
      "user_rating". "user_id" maps to a string tensor that represents the user
      id for the example. "movie_title" maps to a tensor of shape
      [sum(num_example_per_list)] with dtype tf.string. It represents the list
      of candidate movie ids. "user_rating" maps to a tensor of shape
      [sum(num_example_per_list)] with dtype tf.float32. It represents the
      rating of each movie in the candidate list.
  """
  random_state = np.random.RandomState(seed)

  example_lists_by_user = collections.defaultdict(_create_feature_dict)

  document_vocab = set()
  for example in rating_dataset:
    user_id = example["query"].numpy()
    example_lists_by_user[user_id]["body"].append(
        example["body"])
    example_lists_by_user[user_id]["relevance"].append(
        example["relevance"])
    document_vocab.add(example["body"].numpy())

  tensor_slices = {"query": [], "body": [], "relevance": []}

  for user_id, feature_lists in example_lists_by_user.items():
    for _ in range(num_list_per_user):

      # Drop the user if they don't have enough ratings.
      if len(feature_lists["body"]) < num_examples_per_list:
        continue

      sampled_movie_titles, sampled_ratings = _sample_list(
          feature_lists,
          num_examples_per_list,
          random_state=random_state,
      )
      tensor_slices["query"].append(user_id)
      tensor_slices["body"].append(sampled_movie_titles)
      tensor_slices["relevance"].append(sampled_ratings)

  return tf.data.Dataset.from_tensor_slices(tensor_slices)

In [38]:
train = sample_listwise(dataset, 60, 100, 42)

In [39]:
train

<_TensorSliceDataset element_spec={'query': TensorSpec(shape=(), dtype=tf.string, name=None), 'body': TensorSpec(shape=(100,), dtype=tf.string, name=None), 'relevance': TensorSpec(shape=(100,), dtype=tf.string, name=None)}>

In [40]:
for example in train.take(1):
  pprint.pprint(example)

{'body': <tf.Tensor: shape=(100,), dtype=string, numpy=
array([b'effect variety , processing , storage flavonoid glycoside content composition lettuce endive . - pubmed - ncbi abstract eight varieties lettuce ( lactuca sativum ) varieties endive ( cichorium endivia ) analyzed flavonoid composition content . total flavonoid contents , expressed units aglycon fresh material , ranges 0.3-229 microg/g lettuce 44-248 microg/g endive . five quercetin conjugates [ quercetin 3-o-galactoside , quercetin 3-o-glucoside , quercetin 3-o-glucuronide , quercetin 3-o- ( 6-o-malonyl ) glucoside , quercetin 3-o-rhamnoside ] luteolin 7-o-glucuronide measured green-leafed lettuce additional cyanidin conjugates [ cyanidin 3-o-glucoside cyanidin 3-o- [ ( 6-o-malonyl ) glucoside ] ] red-leafed varieties . three kaempferol conjugates [ kaempferol 3-o-glucoside , kaempferol 3-o-glucuronide , kaempferol 3-o- [ 6-o-malonyl ) glucoside ] ] measured endive varieties . the presence identity kaempferol 3-o- ( 6-o-ma

In [41]:
test = sample_listwise(dataset_test, 60, 100, 42)

In [42]:
dev = sample_listwise(dataset_dev, 60, 100, 42)

In [43]:
len(unique_docs)

3594

In [44]:
len(unique_queries)

3220

In [45]:
class RankingModel(tfrs.Model):

  def __init__(self, loss):
    super().__init__()
    embedding_dimension = 400

    # Compute embeddings for users.
    self.user_embeddings = tf.keras.Sequential([
      tf.keras.layers.StringLookup(
        vocabulary=unique_queries),
      tf.keras.layers.Embedding(len(unique_queries) + 2, embedding_dimension)
    ])

    # Compute embeddings for movies.
    self.movie_embeddings = tf.keras.Sequential([
      tf.keras.layers.StringLookup(
        vocabulary=unique_docs),
      tf.keras.layers.Embedding(len(unique_docs) + 2, embedding_dimension)
    ])

    # Compute predictions.
    self.score_model = tf.keras.Sequential([
      # Learn multiple dense layers.
      tf.keras.layers.Dense(1, activation="relu"),
      # tf.keras.layers.Dense(1, activation="relu"),
      # Make rating predictions in the final layer.
      tf.keras.layers.Dense(1)
    ])

    self.task = tfrs.tasks.Ranking(
      loss=loss,
      metrics=[
        tfr.keras.metrics.NDCGMetric(name="ndcg_metric"),
        tf.keras.metrics.RootMeanSquaredError()
      ]
    )

  def call(self, features):
    # We first convert the id features into embeddings.
    # User embeddings are a [batch_size, embedding_dim] tensor.
    user_embeddings = self.user_embeddings(features["query"])

    # Movie embeddings are a [batch_size, num_movies_in_list, embedding_dim]
    # tensor.
    movie_embeddings = self.movie_embeddings(features["body"])

    # We want to concatenate user embeddings with movie emebeddings to pass
    # them into the ranking model. To do so, we need to reshape the user
    # embeddings to match the shape of movie embeddings.
    # for x in features["body"]:
    # pprint.pprint(features["body"])
    list_length = features["body"].shape[1]
    user_embedding_repeated = tf.repeat(
        tf.expand_dims(user_embeddings, 1), [list_length], axis=1)

    # Once reshaped, we concatenate and pass into the dense layers to generate
    # predictions.
    concatenated_embeddings = tf.concat(
        [user_embedding_repeated, movie_embeddings], 2)

    return self.score_model(concatenated_embeddings)

  def compute_loss(self, features, training=False):
    labels = features.pop("relevance")
    labels = tf.strings.to_number(labels)
    print(labels)
    scores = self(features)

    return self.task(
        labels=labels,
        predictions=tf.squeeze(scores, axis=-1),
    )

In [46]:
mse_model = RankingModel(tf.keras.losses.MeanSquaredError())
mse_model.compile(optimizer=tf.keras.optimizers.Adagrad(0.1))

In [47]:
epochs = 30

cached_train = train.shuffle(100_000).batch(2000).cache()
cached_test = test.batch(500).cache()
cached_dev = dev.batch(1000).cache()

In [48]:
mse_model.fit(cached_train, epochs=2, verbose=False)

Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)
Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)


In [49]:
mse_model_result = mse_model.evaluate(cached_test, return_dict=True)
print("NDCG of the MSE Model: {:.4f}".format(mse_model_result["ndcg_metric"]))

Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)
4/4 [==============================] - 1s 161ms/step - ndcg_metric: 0.9484 - root_mean_squared_error: 0.5469 - loss: 0.2931 - regularization_loss: 0.0000e+00 - total_loss: 0.2931
NDCG of the MSE Model: 0.9484


In [50]:
hinge_model = RankingModel(tfr.keras.losses.PairwiseHingeLoss())
hinge_model.compile(optimizer=tf.keras.optimizers.Adagrad(0.1))

In [51]:
hinge_model.fit(cached_train, epochs=epochs, verbose=False)

Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)
Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)


In [52]:
hinge_model_result = hinge_model.evaluate(cached_test, return_dict=True)
print("NDCG of the pairwise hinge loss model: {:.4f}".format(hinge_model_result["ndcg_metric"]))

Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)
4/4 [==============================] - 1s 245ms/step - ndcg_metric: 0.9928 - root_mean_squared_error: 4.2373 - loss: 2.0315 - regularization_loss: 0.0000e+00 - total_loss: 2.0315
NDCG of the pairwise hinge loss model: 0.9928


In [53]:
listwise_model = RankingModel(tfr.keras.losses.ListMLELoss())
listwise_model.compile(optimizer=tf.keras.optimizers.Adagrad(0.1))

In [54]:
listwise_model.fit(cached_train, epochs=epochs, verbose=False)

Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)
Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)


In [55]:
listwise_model_result = listwise_model.evaluate(cached_test, return_dict=True)
print("NDCG of the ListMLE model: {:.4f}".format(listwise_model_result["ndcg_metric"]))

Tensor("StringToNumber:0", shape=(None, 100), dtype=float32)
4/4 [==============================] - 2s 223ms/step - ndcg_metric: 0.9897 - root_mean_squared_error: 2.6220 - loss: 352.8807 - regularization_loss: 0.0000e+00 - total_loss: 352.8807
NDCG of the ListMLE model: 0.9897


In [56]:
listwise_model_result

{'ndcg_metric': 0.9897339940071106,
 'root_mean_squared_error': 2.622022867202759,
 'loss': 358.0739440917969,
 'regularization_loss': 0,
 'total_loss': 358.0739440917969}